In [1]:
# import YOLO model
from ultralytics import YOLO
import cv2
import matplotlib.pyplot as plt
from sklearn.metrics import classification_report, confusion_matrix, accuracy_score, precision_score, recall_score, f1_score
import os

## Comparison between Different Yolo Models
Currently only YOLO v8 and v11 support image classification
- YOLO v8
- YOLO v11


In [2]:
import os

yolo_checkpoints_folder = "/home/etaylor/code_projects/thesis/checkpoints/blur_image_classification/yolo/not_tuned"

yolo_classification_checkpoints = {
    "YOLOv8": {
        "Nano": os.path.join(yolo_checkpoints_folder, "yolov8n-cls.pt"),
        "Small": os.path.join(yolo_checkpoints_folder, "yolov8s-cls.pt"),
        "Medium": os.path.join(yolo_checkpoints_folder, "yolov8m-cls.pt"),
        "Large": os.path.join(yolo_checkpoints_folder, "yolov8l-cls.pt"),
        "XLarge": os.path.join(yolo_checkpoints_folder, "yolov8x-cls.pt"),
    },
        "YOLOv11": {
        "Nano": os.path.join(yolo_checkpoints_folder, "yolo11n-cls.pt"),
        "Small": os.path.join(yolo_checkpoints_folder, "yolo11s-cls.pt"),
        "Medium": os.path.join(yolo_checkpoints_folder, "yolo11m-cls.pt"),
        "Large": os.path.join(yolo_checkpoints_folder, "yolo11l-cls.pt"),
        "XLarge": os.path.join(yolo_checkpoints_folder, "yolo11x-cls.pt"),
    },
}

Functions to fine tune each model and then evaluate it

In [3]:
def train_model(data_path, model_name, model_size, epochs=10, imgsz=128):
    # Load the model checkpoint
    checkpoint = yolo_classification_checkpoints[model_name][model_size]
    model = YOLO(checkpoint)
    
    # Train the model
    model.train(data=data_path, epochs=epochs, imgsz=imgsz)
    
    return model

def eval_model(model, test_data_path):
    # Get class names from the test dataset directory
    class_names = sorted(os.listdir(test_data_path))
    class_to_idx = {class_name: idx for idx, class_name in enumerate(class_names)}

    # Initialize lists for true labels (y_test) and predicted labels (y_pred)
    y_test = []
    y_pred = []

    # Initialize a list to store image data for plotting
    images_for_plotting = []

    # Process each class in the test directory
    for class_name in class_names:
        class_dir = os.path.join(test_data_path, class_name)
        for img_name in os.listdir(class_dir):
            img_path = os.path.join(class_dir, img_name)
            
            # Load the image and run the model prediction
            img = cv2.imread(img_path)
            img_rgb = cv2.cvtColor(img, cv2.COLOR_BGR2RGB)  # Convert to RGB for matplotlib
            results = model(img)
            
            # Get the predicted class index
            predicted_idx = int(results[0].probs.data.argmax())
            
            # Append true and predicted labels
            y_test.append(class_to_idx[class_name])
            y_pred.append(predicted_idx)
            
            # Store the image, true label, and predicted label for plotting
            images_for_plotting.append((img_rgb, class_name, class_names[predicted_idx]))

    # Evaluate using classification metrics
    classification_report_result = classification_report(y_test, y_pred, target_names=class_names)
    accuracy = accuracy_score(y_test, y_pred)
    confusion_matrix_result = confusion_matrix(y_test, y_pred)
    precision = precision_score(y_test, y_pred, average='weighted')
    recall = recall_score(y_test, y_pred, average='weighted')
    f1 = f1_score(y_test, y_pred, average='weighted')
    
    return classification_report_result, accuracy, confusion_matrix_result, precision, recall, f1, images_for_plotting
    
def plot_results(images_for_plotting):
    # Plot images with true and predicted labels
    plt.figure(figsize=(12, 12))
    num_images = len(images_for_plotting)  # Display all images (adjust as needed)
    rows = (num_images // 4) + 1  # Adjust rows based on the number of images

    for i in range(num_images):
        img, true_label, pred_label = images_for_plotting[i]
        plt.subplot(rows, 4, i + 1)  # Dynamic row setting
        plt.imshow(img)
        plt.title(f"True: {true_label}\nPred: {pred_label}", color="green" if true_label == pred_label else "red")
        plt.axis('off')

    plt.tight_layout()
    plt.show()

In [5]:
import os

# iterate over each dataset in the datasets folder
balanced_datasets = "/home/etaylor/code_projects/thesis/classification_datasets/blur_classification/blur_classification_datasets/all_classes/balanced_datasets"
data_paths = [os.path.join(balanced_datasets, dataset) for dataset in os.listdir(balanced_datasets)]

results = []  # List to store the evaluation results

for i, data_path in enumerate(data_paths):
    test_data_path = os.path.join(data_path, "test_balanced")
    # run the functions for each of the models
    for model_name in yolo_classification_checkpoints:
        for model_size in yolo_classification_checkpoints[model_name]:
            print(f"Training {model_name} {model_size} model...")
            model = train_model(data_path, model_name, model_size, epochs=10, imgsz=128)
            
            print(f"Evaluating {model_name} {model_size} model...")
            classification_report_result, accuracy, confusion_matrix_result, precision, recall, f1, images_for_plotting = eval_model(model, test_data_path)
            
            
            # create saving folder if does not exist
            if not os.path.exists(f"/home/etaylor/code_projects/thesis/checkpoints/blur_image_classification/yolo/after_tuning/{model_name}"):
                os.makedirs(f"/home/etaylor/code_projects/thesis/checkpoints/blur_image_classification/yolo/after_tuning/{model_name}")
            
            # save model
            model.save(f"/home/etaylor/code_projects/thesis/checkpoints/blur_image_classification/yolo/after_tuning/{model_name}/{model_size}_dataset_{i}.pt")
            
    
            # Append the evaluation results to the list
            results.append({
                "Model_Name": model_name,
                "Model_Size": model_size,
                "Classification Report": classification_report_result,
                "Accuracy": accuracy,
                "Average Precision": precision,
                "Average Recall": recall,
                "Average f1": f1,
                "Confusion Matrix": confusion_matrix_result,
                "Images for Plotting": images_for_plotting
            })

Training YOLOv8 Nano model...


Ultralytics 8.3.49 🚀 Python-3.9.19 torch-2.3.1+cu121 CUDA:0 (NVIDIA GeForce GTX 1080 Ti, 11165MiB)
engine/trainer: task=classify, mode=train, model=/home/etaylor/code_projects/thesis/checkpoints/blur_image_classification/yolo/not_tuned/yolov8n-cls.pt, data=/home/etaylor/code_projects/thesis/classification_datasets/blur_classification/blur_classification_datasets/all_classes/balanced_datasets/train_set_1, epochs=10, time=None, patience=100, batch=16, imgsz=128, save=True, save_period=-1, cache=False, device=None, workers=8, project=None, name=train187, exist_ok=False, pretrained=True, optimizer=auto, verbose=True, seed=0, deterministic=True, single_cls=False, rect=False, cos_lr=False, close_mosaic=10, resume=False, amp=True, fraction=1.0, profile=False, freeze=None, multi_scale=False, overlap_mask=True, mask_ratio=4, dropout=0.0, val=True, split=val, save_json=False, save_hybrid=False, conf=None, iou=0.7, max_det=300, half=False, dnn=False, plots=True, source=None, vid_stride=1, stream_

train: Scanning /sise/home/etaylor/code_projects/thesis/classification_datasets/blur_classification/blur_classification_datasets/all_classes/balanced_datasets/train_set_1/train... 800 images, 0 corrupt: 100%|██████████| 800/800 [00:00<?, ?it/s]
/home/etaylor/.conda/envs/detectron_fastai/lib/python3.9/site-packages/torch/utils/data/dataloader.py:558: UserWarning: This DataLoader will create 8 worker processes in total. Our suggested max number of worker in current system is 6, which is smaller than what this DataLoader is going to create. Please be aware that excessive worker creation might get DataLoader running slow or even freeze, lower the worker number to avoid potential slowness/freeze if necessary.
  warnings.warn(_create_warning_msg(
val: Scanning /sise/home/etaylor/code_projects/thesis/classification_datasets/blur_classification/blur_classification_datasets/all_classes/balanced_datasets/train_set_1/test... 902 images, 0 corrupt: 100%|██████████| 902/902 [00:00<?, ?it/s]


optimizer: 'optimizer=auto' found, ignoring 'lr0=0.01' and 'momentum=0.937' and determining best 'optimizer', 'lr0' and 'momentum' automatically... 
optimizer: AdamW(lr=0.000714, momentum=0.9) with parameter groups 26 weight(decay=0.0), 27 weight(decay=0.0005), 27 bias(decay=0.0)
TensorBoard: model graph visualization added ✅
Image sizes 128 train, 128 val
Using 8 dataloader workers
Logging results to /home/etaylor/runs/classify/train187
Starting training for 10 epochs...


/home/etaylor/.conda/envs/detectron_fastai/lib/python3.9/site-packages/torch/utils/data/dataloader.py:558: UserWarning: This DataLoader will create 8 worker processes in total. Our suggested max number of worker in current system is 6, which is smaller than what this DataLoader is going to create. Please be aware that excessive worker creation might get DataLoader running slow or even freeze, lower the worker number to avoid potential slowness/freeze if necessary.
  warnings.warn(_create_warning_msg(


...

      10/10      1.55G     0.3588         16        128: 100%|██████████| 50/50 [00:04<00:00, 12.45it/s]
               classes   top1_acc   top5_acc: 100%|██████████| 29/29 [00:00<00:00, 32.53it/s]

                   all      0.871          1



10 epochs completed in 0.045 hours.
Optimizer stripped from /home/etaylor/runs/classify/train280/weights/last.pt, 57.0MB
Optimizer stripped from /home/etaylor/runs/classify/train280/weights/best.pt, 57.0MB

Validating /home/etaylor/runs/classify/train280/weights/best.pt...
Ultralytics 8.3.49 🚀 Python-3.9.19 torch-2.3.1+cu121 CUDA:0 (NVIDIA GeForce GTX 1080 Ti, 11165MiB)
YOLO11x-cls summary (fused): 227 layers, 28,334,978 parameters, 0 gradients, 110.3 GFLOPs
WARNING ⚠️ Dataset 'split=val' not found, using 'split=test' instead.
train: /sise/home/etaylor/code_projects/thesis/classification_datasets/blur_classification/blur_classification_datasets/all_classes/balanced_datasets/train_set_5/train... found 800 images in 2 classes ✅ 
val: None...
test: /sise/home/etaylor/code_projects/thesis/classification_datasets/blur_classification/blur_classification_datasets/all_classes/balanced_datasets/train_set_5/test... found 902 images in 2 classes ✅ 


               classes   top1_acc   top5_acc: 100%|██████████| 29/29 [00:00<00:00, 29.56it/s]


                   all      0.894          1
Speed: 0.0ms preprocess, 1.0ms inference, 0.0ms loss, 0.0ms postprocess per image
Results saved to /home/etaylor/runs/classify/train280
Evaluating YOLOv11 XLarge model...

0: 128x128 blurry 0.84, good_quality 0.16, 7.5ms
Speed: 1.8ms preprocess, 7.5ms inference, 0.1ms postprocess per image at shape (1, 3, 128, 128)

0: 128x128 blurry 0.67, good_quality 0.33, 8.0ms
Speed: 1.6ms preprocess, 8.0ms inference, 0.0ms postprocess per image at shape (1, 3, 128, 128)

0: 128x128 blurry 0.65, good_quality 0.35, 7.8ms
Speed: 1.3ms preprocess, 7.8ms inference, 0.0ms postprocess per image at shape (1, 3, 128, 128)

0: 128x128 blurry 0.63, good_quality 0.37, 7.7ms
Speed: 1.3ms preprocess, 7.7ms inference, 0.0ms postprocess per image at shape (1, 3, 128, 128)

0: 128x128 good_quality 0.72, blurry 0.28, 7.8ms
Speed: 1.3ms preprocess, 7.8ms inference, 0.0ms postprocess per image at shape (1, 3, 128, 128)

0: 128x128 good_quality 0.87, blurry 0.13, 8.0ms
Spee

In [13]:
import pandas as pd

results_df = pd.DataFrame(results)

# sort the results by f1 score
results_df = results_df.sort_values(by="Average f1", ascending=False)

results_df

Model_Name Model_Size                              Classification Report  \
21     YOLOv8      Small                precision    recall  f1-score   ...   
43     YOLOv8      Large                precision    recall  f1-score   ...   
45    YOLOv11       Nano                precision    recall  f1-score   ...   
20     YOLOv8       Nano                precision    recall  f1-score   ...   
30     YOLOv8       Nano                precision    recall  f1-score   ...   
38    YOLOv11      Large                precision    recall  f1-score   ...   
23     YOLOv8      Large                precision    recall  f1-score   ...   
35    YOLOv11       Nano                precision    recall  f1-score   ...   
4      YOLOv8     XLarge                precision    recall  f1-score   ...   
22     YOLOv8     Medium                precision    recall  f1-score   ...   
36    YOLOv11      Small                precision    recall  f1-score   ...   
34     YOLOv8     XLarge                precision    recall  f1-score   ...   
39    YOLOv11     XLarge                precision    recall  f1-score   ...   
19    YOLOv11     XLarge                precision    recall  f1-score   ...   
48    YOLOv11      Large                precision    recall  f1-score   ...   
3      YOLOv8      Large                precision    recall  f1-score   ...   
33     YOLOv8      Large                precision    recall  f1-score   ...   
29    YOLOv11     XLarge                precision    recall  f1-score   ...   
27    YOLOv11     Medium                precision    recall  f1-score   ...   
24     YOLOv8     XLarge                precision    recall  f1-score   ...   
16    YOLOv11      Small                precision    recall  f1-score   ...   
13     YOLOv8      Large                precision    recall  f1-score   ...   
10     YOLOv8       Nano                precision    recall  f1-score   ...   
0      YOLOv8       Nano                precision    recall  f1-score   ...   
2      YOLOv8     Medium                precision    recall  f1-score   ...   
28    YOLOv11      Large                precision    recall  f1-score   ...   
32     YOLOv8     Medium                precision    recall  f1-score   ...   
41     YOLOv8      Small                precision    recall  f1-score   ...   
47    YOLOv11     Medium                precision    recall  f1-score   ...   
6     YOLOv11      Small                precision    recall  f1-score   ...   
44     YOLOv8     XLarge                precision    recall  f1-score   ...   
40     YOLOv8       Nano                precision    recall  f1-score   ...   
12     YOLOv8     Medium                precision    recall  f1-score   ...   
31     YOLOv8      Small                precision    recall  f1-score   ...   
46    YOLOv11      Small                precision    recall  f1-score   ...   
9     YOLOv11     XLarge                precision    recall  f1-score   ...   
1      YOLOv8      Small                precision    recall  f1-score   ...   
14     YOLOv8     XLarge                precision    recall  f1-score   ...   
25    YOLOv11       Nano                precision    recall  f1-score   ...   
26    YOLOv11      Small                precision    recall  f1-score   ...   
11     YOLOv8      Small                precision    recall  f1-score   ...   
7     YOLOv11     Medium                precision    recall  f1-score   ...   
49    YOLOv11     XLarge                precision    recall  f1-score   ...   
18    YOLOv11      Large                precision    recall  f1-score   ...   
37    YOLOv11     Medium                precision    recall  f1-score   ...   
17    YOLOv11     Medium                precision    recall  f1-score   ...   
42     YOLOv8     Medium                precision    recall  f1-score   ...   
8     YOLOv11      Large                precision    recall  f1-score   ...   
15    YOLOv11       Nano                precision    recall  f1-score   ...   
5     YOLOv11       Nano                precision    

In [7]:
results_df.to_csv("/home/etaylor/code_projects/thesis/src/classification/notebooks/blur_classification/evaluation_results/yolo_blur_classification_results_13_12_2024.csv", index=False)

In [8]:
# create an average result dataframe for each of the models
average_results = []

for model_name in yolo_classification_checkpoints:
    for model_size in yolo_classification_checkpoints[model_name]:
        model_results = results_df[(results_df["Model_Name"] == model_name) & (results_df["Model_Size"] == model_size)]
        
        # Calculate the average accuracy
        avg_accuracy = model_results["Accuracy"].mean()
        avg_precision = model_results["Average Precision"].mean()
        avg_recall = model_results["Average Recall"].mean()
        avg_f1 = model_results["Average f1"].mean()
        
        # Calculate the average confusion matrix
        avg_confusion_matrix = model_results["Confusion Matrix"].mean(axis=0)
        
        # Append the average results to the list
        average_results.append({
            "Model Name": model_name,
            "Model Size": model_size,
            "Average Accuracy": avg_accuracy,
            "Average Precision": avg_precision,
            "Average Recall": avg_recall,
            "Average f1": avg_f1,
            "Average Confusion Matrix": avg_confusion_matrix
        })

In [9]:
average_results_df = pd.DataFrame(average_results)
average_results_df

Model Name Model Size  Average Accuracy  Average Precision  Average Recall  \
0     YOLOv8       Nano          0.852551           0.854959        0.852551   
1     YOLOv8      Small          0.841327           0.846499        0.841327   
2     YOLOv8     Medium          0.839286           0.846231        0.839286   
3     YOLOv8      Large          0.857653           0.860336        0.857653   
4     YOLOv8     XLarge          0.847449           0.854074        0.847449   
5    YOLOv11       Nano          0.832653           0.839147        0.832653   
6    YOLOv11      Small          0.840306           0.845658        0.840306   
7    YOLOv11     Medium          0.828571           0.838952        0.828571   
8    YOLOv11      Large          0.838265           0.849154        0.838265   
9    YOLOv11     XLarge          0.843878           0.854657        0.843878   

   Average f1        Average Confusion Matrix  
0    0.852287  [[161.2, 34.8], [23.0, 173.0]]  
1    0.840680  [[153.8, 42.2], [20.0, 176.0]]  
2    0.838414  [[151.6, 44.4], [18.6, 177.4]]  
3    0.857384  [[160.0, 36.0], [19.8, 176.2]]  
4    0.846686  [[154.6, 41.4], [18.4, 177.6]]  
5    0.831661  [[151.4, 44.6], [21.0, 175.0]]  
6    0.839642  [[154.0, 42.0], [20.6, 175.4]]  
7    0.827243  [[145.6, 50.4], [16.8, 179.2]]  
8    0.836832  [[148.2, 47.8], [15.6, 180.4]]  
9    0.842588  [[149.4, 46.6], [14.6, 181.4]]

In [10]:
# save the results to a file
average_results_df.to_csv("/home/etaylor/code_projects/thesis/src/classification/notebooks/blur_classification/evaluation_results/yolo_blur_classification_avg_results_for_5_datasets_13_12_2024.csv", index=False)

In [36]:
print(average_results_df.columns)

Index(['Model Name', 'Model Size', 'Average Accuracy', 'Average Precision',
       'Average Recall', 'Average f1', 'Average Confusion Matrix'],
      dtype='object')


In [15]:
%matplotlib inline

In [11]:
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns

# Convert the average results to a DataFrame
average_results_df = pd.DataFrame(average_results)

# Plot the key metrics (accuracy, precision, recall, F1) across different models and sizes
metrics = ["Average Accuracy", "Average Precision", "Average Recall", "Average f1"]

plt.figure(figsize=(16, 12))

for i, metric in enumerate(metrics, 1):
    plt.subplot(2, 2, i)
    sns.barplot(data=average_results_df, x="Model Size", y=metric, hue="Model Name")
    plt.title(f"Comparison of {metric} Across Models and Sizes")
    plt.ylabel(metric)
    plt.xlabel("Model Size")
    plt.legend(title="Model Name")

plt.tight_layout()
plt.show()


<Figure size 1600x1200 with 4 Axes>

In [12]:
import matplotlib.pyplot as plt
import seaborn as sns

# Define the number of rows and columns for the grid
num_matrices = len(average_results_df)
ncols = 3  # Number of columns in the grid
nrows = (num_matrices // ncols) + (num_matrices % ncols > 0)  # Calculate rows needed

# Set up the figure for the grid of confusion matrices
fig, axes = plt.subplots(nrows=nrows, ncols=ncols, figsize=(ncols * 5, nrows * 5))

# Flatten axes to easily iterate over them
axes = axes.flatten()

# Plot each confusion matrix in the grid
for index, (ax, row) in enumerate(zip(axes, average_results_df.iterrows())):
    row_data = row[1]
    sns.heatmap(row_data["Average Confusion Matrix"], annot=True, fmt=".2f", cmap="Blues", cbar=True, ax=ax)
    ax.set_title(f"{row_data['Model Name']} - {row_data['Model Size']}")
    ax.set_xlabel("Predicted Class")
    ax.set_ylabel("True Class")

# Remove any unused subplots
for i in range(num_matrices, len(axes)):
    fig.delaxes(axes[i])

plt.tight_layout()
plt.show()


<Figure size 1500x2000 with 20 Axes>

## Experiment Settings
- class 0 = blurry, class 1 = good_quality
- 550 Images for train
- 195 Images for test

## Experiment results
- Good Results
- Around 93% for all metrics (accuracy, precision, recall and f1)
- In conf matrix class 0 = amber, 1 = clear and 2 = cloudy
- Best model to predict amber class is yolov8 Large.
